In [89]:
import psycopg2
import pandas as pd
import numpy as np
import plotly.express as px

# pgparams = {
#     "database": "ofetdb_testenv",
#     "user":"postgres",
#     "password":"password",
#     "host": "127.0.0.1",
#     "port": "5432"
#     }

# pgparams = {
#     "host": "127.0.0.1",
#     "database": "ofetdb_testenv",
#     "user": "postgres",
#     "password": "Rahul2411!",
#     "port": "5432",
# }


# Set max number of displayed columns and rows in Jupyter Notebook
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)


pgparams = {
    "host": "chbe-ofet-db.postgres.database.azure.com",
    "database": "ofetdb_v2",
    "user": "mg200_ofetdb",
    "password": "MGEROFETDB23!",
    "port": "5432",
}

def read_select_query(query):

    with psycopg2.connect(**pgparams) as conn:

        df = pd.read_sql_query(query, conn)

    return df


## Simplest Scenario :

- assume only single polymer scenarios, no blends first (wt_frac = 1)
- assume only single solvent scenarios, no multiple solvents (vol_frac = 1)
- show device substrate information (go into detail of parameters)
- show film deposition information only no need for parameters
- dont go into detail of solution treatment, substrate pretreat and post process
- show hole mobility information

In [90]:
# ## Adding all the experiment information 

# # SQL query to fetch the required data
# query = '''
#     SELECT
#         s.sample_id,
#         e.citation_type,
#         e.meta as experiment_meta
#     FROM
#         SAMPLE s
#     JOIN
#         EXPERIMENT_INFO e ON s.exp_id = e.exp_id;
# '''

# # Use the read_select_query function to execute the query
# result_df = read_select_query(query)

# # Display the resulting DataFrame
# #print(result_df)

# result_df

In [91]:
# ## Adding all the solution_concentration information 

# query = '''
#     SELECT
#         s.sample_id,
#         e.citation_type,
#         e.meta as experiment_meta,
#         sol.concentration as solution_concentration
#     FROM
#         SAMPLE s
#     JOIN
#         EXPERIMENT_INFO e ON s.exp_id = e.exp_id
#     LEFT JOIN
#         OFET_PROCESS op ON s.process_id = op.process_id
#     LEFT JOIN
#         SOLUTION sol ON op.solution_id = sol.solution_id;
# '''

# # Use the read_select_query function to execute the query
# result_df = read_select_query(query)

# # Display the resulting DataFrame
# result_df

In [92]:
# #adding solvent information (only adding devices made from single solvent vol frac = 1)

# import pandas as pd
# import psycopg2

# pgparams = {
#     "host": "chbe-ofet-db.postgres.database.azure.com",
#     "database": "ofetdb_v2",
#     "user": "mg200_ofetdb",
#     "password": "MGEROFETDB23!",
#     "port": "5432",
# }

# def read_select_query(query):
#     with psycopg2.connect(**pgparams) as conn:
#         df = pd.read_sql_query(query, conn)
#     return df

# # SQL query to fetch the required data
# query = '''
#     SELECT
#         s.sample_id,
#         e.citation_type,
#         e.meta as experiment_meta,
#         sol.concentration as solution_concentration,
#         sm_s.vol_frac as solvent_vol_frac,
#         sv.pubchem_cid as solvent_pubchem_cid,
#         sv.iupac_name as solvent_iupac_name
#     FROM
#         SAMPLE s
#     JOIN
#         EXPERIMENT_INFO e ON s.exp_id = e.exp_id
#     LEFT JOIN
#         OFET_PROCESS op ON s.process_id = op.process_id
#     LEFT JOIN
#         SOLUTION sol ON op.solution_id = sol.solution_id
#     LEFT JOIN
#         SOLUTION_MAKEUP_SOLVENT sm_s ON sol.solution_id = sm_s.solution_id
#     LEFT JOIN
#         SOLVENT sv ON sm_s.solvent_id = sv.pubchem_cid
#     WHERE
#         sm_s.vol_frac = 1;
# '''

# # Use the read_select_query function to execute the query
# result_df = read_select_query(query)

# # Display the resulting DataFrame
# result_df


In [93]:
## adding solvent boiling point to the dataframe - this takes time

# import requests
# import pandas as pd
# from IPython.display import display

# # Function to get boiling point from PubChem
# def get_boiling_point(pubchem_cid):
#     api_url = f'https://pubchem.ncbi.nlm.nih.gov/rest/pug/compound/cid/{pubchem_cid}/json'
#     response = requests.get(api_url)
    
#     if response.status_code == 200:
#         data = response.json()
#         if 'PropertyTable' in data and 'Boiling Point' in data['PropertyTable']:
#             return data['PropertyTable']['Boiling Point']['Value']
    
#     return None

# # Add a new column 'solvent_boiling_point' to the DataFrame
# result_df['solvent_boiling_point'] = result_df['solvent_pubchem_cid'].apply(get_boiling_point)

# result_df

In [94]:
# ## adding polymer information only for devices made from one polymer (no blends) (wt-frac = 1)



# import pandas as pd
# import psycopg2

# pgparams = {
#     "host": "chbe-ofet-db.postgres.database.azure.com",
#     "database": "ofetdb_v2",
#     "user": "mg200_ofetdb",
#     "password": "MGEROFETDB23!",
#     "port": "5432",
# }

# def read_select_query(query):
#     with psycopg2.connect(**pgparams) as conn:
#         df = pd.read_sql_query(query, conn)
#     return df

# # SQL query to fetch the required data
# query ='''
#     SELECT
#         s.sample_id,
#         e.citation_type,
#         e.meta as experiment_meta,
#         sol.concentration as solution_concentration,
#         sm_s.vol_frac as solvent_vol_frac,
#         sm_p.wt_frac as polymer_wt_frac,
#         sv.pubchem_cid as solvent_pubchem_cid,
#         sv.iupac_name as solvent_iupac_name,
#         p.common_name as polymer_common_name,
#         p.iupac_name as polymer_iupac_name,
#         p.mw as polymer_mw,
#         p.mn as polymer_mn,
#         p.dispersity as polymer_dispersity
#     FROM
#         SAMPLE s
#     JOIN
#         EXPERIMENT_INFO e ON s.exp_id = e.exp_id
#     LEFT JOIN
#         OFET_PROCESS op ON s.process_id = op.process_id
#     LEFT JOIN
#         SOLUTION sol ON op.solution_id = sol.solution_id
#     LEFT JOIN
#         SOLUTION_MAKEUP_SOLVENT sm_s ON sol.solution_id = sm_s.solution_id AND sm_s.vol_frac = 1
#     LEFT JOIN
#         SOLVENT sv ON sm_s.solvent_id = sv.pubchem_cid
#     LEFT JOIN
#         SOLUTION_MAKEUP_POLYMER sm_p ON sol.solution_id = sm_p.solution_id AND sm_p.wt_frac = 1
#     LEFT JOIN
#         POLYMER p ON sm_p.polymer_id = p.polymer_id
#     WHERE
#         sm_s.vol_frac = 1 AND sm_p.wt_frac = 1;
# '''

# # Use the read_select_query function to execute the query
# result_df = read_select_query(query)

# # Display the resulting DataFrame
# result_df


# ### NOTE THERE ARE SAMPLES WITH INCOMPLETE POLYMER INFORMATION (missing mw, pdi or mn)

In [95]:
# #adding the device substrate information


# import pandas as pd
# import psycopg2

# pgparams = {
#     "host": "chbe-ofet-db.postgres.database.azure.com",
#     "database": "ofetdb_v2",
#     "user": "mg200_ofetdb",
#     "password": "MGEROFETDB23!",
#     "port": "5432",
# }

# def read_select_query(query):
#     with psycopg2.connect(**pgparams) as conn:
#         df = pd.read_sql_query(query, conn)
#     return df

# # SQL query to fetch the required data
# query ='''
#     SELECT
#         s.sample_id,
#         e.citation_type,
#         e.meta as experiment_meta,
#         sol.concentration as solution_concentration,
#         sm_s.vol_frac as solvent_vol_frac,
#         sv.pubchem_cid as solvent_pubchem_cid,
#         sv.iupac_name as solvent_iupac_name,
#         p.common_name as polymer_common_name,
#         p.iupac_name as polymer_iupac_name,
#         p.mw as polymer_mw,
#         p.mn as polymer_mn,
#         p.dispersity as polymer_dispersity,
#         df.params as device_substrate_parameters
#     FROM
#         SAMPLE s
#     JOIN
#         EXPERIMENT_INFO e ON s.exp_id = e.exp_id
#     LEFT JOIN
#         OFET_PROCESS op ON s.process_id = op.process_id
#     LEFT JOIN
#         SOLUTION sol ON op.solution_id = sol.solution_id
#     LEFT JOIN
#         SOLUTION_MAKEUP_SOLVENT sm_s ON sol.solution_id = sm_s.solution_id
#     LEFT JOIN
#         SOLVENT sv ON sm_s.solvent_id = sv.pubchem_cid
#     LEFT JOIN
#         SOLUTION_MAKEUP_POLYMER sm_p ON sol.solution_id = sm_p.solution_id
#     LEFT JOIN
#         POLYMER p ON sm_p.polymer_id = p.polymer_id
#     LEFT JOIN
#         DEVICE_FABRICATION df ON op.device_fab_id = df.device_fab_id
#     WHERE
#         sm_s.vol_frac = 1 AND
#         sm_p.wt_frac = 1;
# '''


# # Use the read_select_query function to execute the query
# result_df = read_select_query(query)

# # Display the resulting DataFrame
# result_df



# #### NOTE : There are three samples 21, 22 and 23 that do not have any device fabrication information

In [96]:
# #unpacking the information stored in device_substrate_parameters

# import pandas as pd
# from pandas import json_normalize



# # Extract the 'device_substrate_parameters' column and normalize it
# params_df = json_normalize(result_df['device_substrate_parameters'])

# # Concatenate the original DataFrame with the new 'params_df'
# result_df = pd.concat([result_df, params_df], axis=1)

# # Drop the original 'device_substrate_parameters' column
# result_df = result_df.drop('device_substrate_parameters', axis=1)

# # Display the resulting DataFrame
# result_df


In [97]:
# #adding the device substrate information


# import pandas as pd
# import psycopg2

# pgparams = {
#     "host": "chbe-ofet-db.postgres.database.azure.com",
#     "database": "ofetdb_v2",
#     "user": "mg200_ofetdb",
#     "password": "MGEROFETDB23!",
#     "port": "5432",
# }

# def read_select_query(query):
#     with psycopg2.connect(**pgparams) as conn:
#         df = pd.read_sql_query(query, conn)
#     return df

# # SQL query to fetch the required data
# query ='''
#     SELECT
#         s.sample_id,
#         e.citation_type,
#         e.meta as experiment_meta,
#         sol.concentration as solution_concentration,
#         sm_s.vol_frac as solvent_vol_frac,
#         sv.pubchem_cid as solvent_pubchem_cid,
#         sv.iupac_name as solvent_iupac_name,
#         p.common_name as polymer_common_name,
#         p.iupac_name as polymer_iupac_name,
#         p.mw as polymer_mw,
#         p.mn as polymer_mn,
#         p.dispersity as polymer_dispersity,
#         df.params as device_substrate_parameters,
#         fd.deposition_type as film_deposition_type,
#         fd.params as film_deposition_params
#     FROM
#         SAMPLE s
#     JOIN
#         EXPERIMENT_INFO e ON s.exp_id = e.exp_id
#     LEFT JOIN
#         OFET_PROCESS op ON s.process_id = op.process_id
#     LEFT JOIN
#         SOLUTION sol ON op.solution_id = sol.solution_id
#     LEFT JOIN
#         SOLUTION_MAKEUP_SOLVENT sm_s ON sol.solution_id = sm_s.solution_id
#     LEFT JOIN
#         SOLVENT sv ON sm_s.solvent_id = sv.pubchem_cid
#     LEFT JOIN
#         SOLUTION_MAKEUP_POLYMER sm_p ON sol.solution_id = sm_p.solution_id
#     LEFT JOIN
#         POLYMER p ON sm_p.polymer_id = p.polymer_id
#     LEFT JOIN
#         DEVICE_FABRICATION df ON op.device_fab_id = df.device_fab_id
#     LEFT JOIN
#         FILM_DEPOSITION fd ON op.film_deposition_id = fd.film_deposition_id
#     WHERE
#         sm_s.vol_frac = 1 AND
#         sm_p.wt_frac = 1;
# '''


# # Use the read_select_query function to execute the query
# result_df = read_select_query(query)

# # Display the resulting DataFrame
# result_df



In [98]:
# #adding the hole mobility information. only adding hole_mobility not NAN. getting rid of NAN


# import pandas as pd
# import psycopg2

# pgparams = {
#     "host": "chbe-ofet-db.postgres.database.azure.com",
#     "database": "ofetdb_v2",
#     "user": "mg200_ofetdb",
#     "password": "MGEROFETDB23!",
#     "port": "5432",
# }

# def read_select_query(query):
#     with psycopg2.connect(**pgparams) as conn:
#         df = pd.read_sql_query(query, conn)
#     return df

# # SQL query to fetch the required data
# query ='''
#     SELECT
#         s.sample_id,
#         e.citation_type,
#         e.meta as experiment_meta,
#         sol.concentration as solution_concentration,
#         sm_s.vol_frac as solvent_vol_frac,
#         sv.pubchem_cid as solvent_pubchem_cid,
#         sv.iupac_name as solvent_iupac_name,
#         p.common_name as polymer_common_name,
#         p.iupac_name as polymer_iupac_name,
#         p.mw as polymer_mw,
#         p.mn as polymer_mn,
#         p.dispersity as polymer_dispersity,
#         df.params as device_substrate_parameters,
#         fd.deposition_type as film_deposition_type,
#         fd.params as film_deposition_params,
#         CAST(m.data -> 'hole_mobility' ->> 'value' AS FLOAT) AS hole_mobility
#     FROM
#         SAMPLE s
#     JOIN
#         EXPERIMENT_INFO e ON s.exp_id = e.exp_id
#     LEFT JOIN
#         OFET_PROCESS op ON s.process_id = op.process_id
#     LEFT JOIN
#         SOLUTION sol ON op.solution_id = sol.solution_id
#     LEFT JOIN
#         SOLUTION_MAKEUP_SOLVENT sm_s ON sol.solution_id = sm_s.solution_id
#     LEFT JOIN
#         SOLVENT sv ON sm_s.solvent_id = sv.pubchem_cid
#     LEFT JOIN
#         SOLUTION_MAKEUP_POLYMER sm_p ON sol.solution_id = sm_p.solution_id
#     LEFT JOIN
#         POLYMER p ON sm_p.polymer_id = p.polymer_id
#     LEFT JOIN
#         DEVICE_FABRICATION df ON op.device_fab_id = df.device_fab_id
#     LEFT JOIN
#         FILM_DEPOSITION fd ON op.film_deposition_id = fd.film_deposition_id
#     LEFT JOIN
#         MEASUREMENT m ON s.sample_id = m.sample_id
#     WHERE
#         sm_s.vol_frac = 1 AND
#         sm_p.wt_frac = 1 AND
#         m.measurement_type = 'transfer_curve' AND
#         m.data -> 'hole_mobility' ->> 'value' IS NOT NULL;
# '''


# # Use the read_select_query function to execute the query
# result_df = read_select_query(query)

# # Display the resulting DataFrame
# result_df



In [99]:
## Now need to add solution treatment, substrate_pretreat and post process info

# 1 if treatment is done and 0 if no treatment

#adding the hole mobility information. only adding hole_mobility not NAN. getting rid of NAN


import pandas as pd
import psycopg2

pgparams = {
    "host": "chbe-ofet-db.postgres.database.azure.com",
    "database": "ofetdb_v2",
    "user": "mg200_ofetdb",
    "password": "MGEROFETDB23!",
    "port": "5432",
}

def read_select_query(query):
    with psycopg2.connect(**pgparams) as conn:
        df = pd.read_sql_query(query, conn)
    return df

# SQL query to fetch the required data
query ='''
    SELECT
        s.sample_id,
        e.citation_type,
        e.meta as experiment_meta,
        sol.concentration as solution_concentration,
        sm_s.vol_frac as solvent_vol_frac,
        sv.pubchem_cid as solvent_pubchem_cid,
        sv.iupac_name as solvent_iupac_name,
        p.common_name as polymer_common_name,
        p.iupac_name as polymer_iupac_name,
        p.mw as polymer_mw,
        p.mn as polymer_mn,
        p.dispersity as polymer_dispersity,
        df.params as device_substrate_parameters,
        fd.deposition_type as film_deposition_type,
        fd.params as film_deposition_params,
        CAST(m.data -> 'hole_mobility' ->> 'value' AS FLOAT) AS hole_mobility,
        CASE WHEN op.solution_treatment_id IS NOT NULL THEN 1 ELSE 0 END AS Solution_treatment,
        CASE WHEN op.substrate_pretreat_id IS NOT NULL THEN 1 ELSE 0 END AS Substrate_pretreatment,
        CASE WHEN op.postprocess_id IS NOT NULL THEN 1 ELSE 0 END AS Post_Process
    FROM
        SAMPLE s
    JOIN
        EXPERIMENT_INFO e ON s.exp_id = e.exp_id
    LEFT JOIN
        OFET_PROCESS op ON s.process_id = op.process_id
    LEFT JOIN
        SOLUTION sol ON op.solution_id = sol.solution_id
    LEFT JOIN
        SOLUTION_MAKEUP_SOLVENT sm_s ON sol.solution_id = sm_s.solution_id
    LEFT JOIN
        SOLVENT sv ON sm_s.solvent_id = sv.pubchem_cid
    LEFT JOIN
        SOLUTION_MAKEUP_POLYMER sm_p ON sol.solution_id = sm_p.solution_id
    LEFT JOIN
        POLYMER p ON sm_p.polymer_id = p.polymer_id
    LEFT JOIN
        DEVICE_FABRICATION df ON op.device_fab_id = df.device_fab_id
    LEFT JOIN
        FILM_DEPOSITION fd ON op.film_deposition_id = fd.film_deposition_id
    LEFT JOIN
        MEASUREMENT m ON s.sample_id = m.sample_id
    WHERE
        sm_s.vol_frac = 1 AND
        sm_p.wt_frac = 1 AND
        m.measurement_type = 'transfer_curve' AND
        m.data -> 'hole_mobility' ->> 'value' IS NOT NULL;
'''


# Use the read_select_query function to execute the query
result_df = read_select_query(query)

# Display the resulting DataFrame
result_df

sample_id citation_type  \
0            1    literature   
1            2    literature   
2            3    literature   
3            4    literature   
4            5    literature   
5            6    literature   
6            7    literature   
7            8    literature   
8            9    literature   
9           10    literature   
10          11    literature   
11          12    literature   
12          21    literature   
13          22    literature   
14          23    literature   
15          24    literature   
16          25    literature   
17          26    literature   
18          27    literature   
19          28    literature   
20          29    literature   
21          30    literature   
22          31    literature   
23          32    literature   
24          33    literature   
25          34    literature   
26          35    literature   
27          43    literature   
28          44    literature   
29          45    literature   
30          46    literature   
31          47    literature   
32          48    literature   
33          49    literature   
34          50    literature   
35          51    literature   
36          52    literature   
37          53    literature   
38          54    literature   
39          55    literature   
40          56    literature   
41          57    literature   
42          58    literature   
43          59    literature   
44          60    literature   
45          61    literature   
46          62    literature   
47          63    literature   
48          64    literature   
49          65    literature   
50          66    literature   
51          67    literature   
52          68    literature   
53          75    literature   
54          81    literature   
55          82    literature   
56          83    literature   
57          84    literature   
58          85    literature   
59          86    literature   
60          87    literature   
61          88    literature   
62          89    literature   
63          90    literature   
64          91    literature   
65          92    literature   
66          93    literature   
67          94    literature   
68          95    literature   
69          96    literature   
70          97    literature   
71          98    literature   
72          99    literature   
73         100    literature   
74         101    literature   
75         102    literature   
76         103    literature   
77         104    literature   
78         105    literature   
79         106    literature   
80         107    literature   
81         108    literature   
82         109    literature   
83         110    literature   
84         111    literature   
85         112    literature   
86         113    literature   
87         114    literature   
88         115    literature   
89         116    literature   
90         117    literature   
91         118    literature   
92         119    literature   
93         120    literature   
94         121    literature   
95         122    literature   
96         123    literature   
97         124    literature   
98         125    literature   
99         126    literature   
100        127    literature   
101        128    literature   
102        129    literature   
103        130    literature   
104        131    literature   
105        132    literature   
106        133    literature   
107        134    literature   
108        135    literature   
109        136    laboratory   
110        137    laboratory   
111        138    laboratory   
112        139    laboratory   
113        140    laboratory   
114        141    laboratory   
115        142    laboratory   
116        143    laboratory   
117        190    literature   
118        144    laboratory   
119        149    laboratory   
120        154    laboratory   
121        159    laboratory   
122        160    laboratory   
123        161    laboratory   
124  

#### This is probably the simplest table you can have. 

- should remove the film deposition parameters and just keep the film deposition type and OHE it
- then unwrap the device substrate parameters
- then split into DPP-DTT(and DPP-2TT), P3HT

In [100]:
 #unpacking the information stored in device_substrate_parameters

import pandas as pd
from pandas import json_normalize



# # Extract the 'device_substrate_parameters' column and normalize it
params_df = json_normalize(result_df['device_substrate_parameters'])

# # Concatenate the original DataFrame with the new 'params_df'
result_df = pd.concat([result_df, params_df], axis=1)

# # Drop the original 'device_substrate_parameters' column
result_df = result_df.drop('device_substrate_parameters', axis=1)

# # Display the resulting DataFrame
result_df

sample_id citation_type  \
0            1    literature   
1            2    literature   
2            3    literature   
3            4    literature   
4            5    literature   
5            6    literature   
6            7    literature   
7            8    literature   
8            9    literature   
9           10    literature   
10          11    literature   
11          12    literature   
12          21    literature   
13          22    literature   
14          23    literature   
15          24    literature   
16          25    literature   
17          26    literature   
18          27    literature   
19          28    literature   
20          29    literature   
21          30    literature   
22          31    literature   
23          32    literature   
24          33    literature   
25          34    literature   
26          35    literature   
27          43    literature   
28          44    literature   
29          45    literature   
30          46    literature   
31          47    literature   
32          48    literature   
33          49    literature   
34          50    literature   
35          51    literature   
36          52    literature   
37          53    literature   
38          54    literature   
39          55    literature   
40          56    literature   
41          57    literature   
42          58    literature   
43          59    literature   
44          60    literature   
45          61    literature   
46          62    literature   
47          63    literature   
48          64    literature   
49          65    literature   
50          66    literature   
51          67    literature   
52          68    literature   
53          75    literature   
54          81    literature   
55          82    literature   
56          83    literature   
57          84    literature   
58          85    literature   
59          86    literature   
60          87    literature   
61          88    literature   
62          89    literature   
63          90    literature   
64          91    literature   
65          92    literature   
66          93    literature   
67          94    literature   
68          95    literature   
69          96    literature   
70          97    literature   
71          98    literature   
72          99    literature   
73         100    literature   
74         101    literature   
75         102    literature   
76         103    literature   
77         104    literature   
78         105    literature   
79         106    literature   
80         107    literature   
81         108    literature   
82         109    literature   
83         110    literature   
84         111    literature   
85         112    literature   
86         113    literature   
87         114    literature   
88         115    literature   
89         116    literature   
90         117    literature   
91         118    literature   
92         119    literature   
93         120    literature   
94         121    literature   
95         122    literature   
96         123    literature   
97         124    literature   
98         125    literature   
99         126    literature   
100        127    literature   
101        128    literature   
102        129    literature   
103        130    literature   
104        131    literature   
105        132    literature   
106        133    literature   
107        134    literature   
108        135    literature   
109        136    laboratory   
110        137    laboratory   
111        138    laboratory   
112        139    laboratory   
113        140    laboratory   
114        141    laboratory   
115        142    laboratory   
116        143    laboratory   
117        190    literature   
118        144    laboratory   
119        149    laboratory   
120        154    laboratory   
121        159    laboratory   
122        160    laboratory   
123        161    laboratory   
124  

In [101]:

# Drop unnecessary columns that won't be used for modeling
columns_to_drop = ['film_deposition_params', 'citation_type', 'experiment_meta', 'solvent_vol_frac', 'solvent_iupac_name', 'polymer_iupac_name', 'dielectric_material_2', 'dielectric_thickness_2', 'dielectric_1_material', 'dielectric_1_thickness', 'substrate_material']
result_df = result_df.drop(columns=columns_to_drop)

# Display the resulting DataFrame
result_df


sample_id  solution_concentration  solvent_pubchem_cid  \
0            1                   4.000                 7964   
1            2                   4.000                 7964   
2            3                   4.000                 7964   
3            4                   4.000                 7964   
4            5                   4.000                 7964   
5            6                   4.000                 7964   
6            7                   4.000                 7964   
7            8                   4.000                 7964   
8            9                   4.000                 7964   
9           10                   4.000                 7964   
10          11                   4.000                 7964   
11          12                   5.000                 6212   
12          21                   5.000                 7964   
13          22                   5.000                 7964   
14          23                   5.000                 7964   
15          24                   5.000                 7964   
16          25                   5.000                 7964   
17          26                   5.000                 7964   
18          27                   5.000                 7964   
19          28                   5.000                 7964   
20          29                   5.000                 7964   
21          30                   5.000                 7964   
22          31                   5.000                 7964   
23          32                   5.000                 7964   
24          33                   5.000                 7964   
25          34                   5.000                 7964   
26          35                   4.000                 7239   
27          43                   6.500                 6212   
28          44                   6.500                 6212   
29          45                   6.500                 6212   
30          46                   6.500                 6212   
31          47                   6.500                 6212   
32          48                   6.500                 6212   
33          49                   6.500                 6212   
34          50                   6.500                 6212   
35          51                   3.000                 7239   
36          52                   3.000                 7239   
37          53                   7.000                 7239   
38          54                   7.000                 7239   
39          55                   6.500                 6212   
40          56                   1.600                 6212   
41          57                   1.600                 6212   
42          58                   0.500                 6212   
43          59                   0.750                 6212   
44          60                   1.000                 6212   
45          61                   2.000                 6212   
46          62                   5.000                 6212   
47          63                   0.500                 6212   
48          64                   0.750                 6212   
49          65                   1.000                 6212   
50          66                   2.000                 6212   
51          67                   5.000                 6212   
52          68                   2.000                 7239   
53          75                   4.000                 6212   
54          81                   5.000                 6212   
55          82                   5.000                 6212   
56          83                   5.000                 6212   
57          84                   7.000                 6212   
58          85                   8.500                 6212   
59          86                  10.000                 6212   
60          87                  12.000                 6212   
61          88                  14.000                 6212   
62          89                  16.0

In [102]:
# List of columns to one-hot encode
columns_to_one_hot_encode = ['film_deposition_type', 'gate_material', 'dielectric_material', 'electrode_configuration']

# Perform one-hot encoding
result_df = pd.get_dummies(result_df, columns=columns_to_one_hot_encode)

# Display the resulting DataFrame with one-hot encoding
result_df


sample_id  solution_concentration  solvent_pubchem_cid  \
0            1                   4.000                 7964   
1            2                   4.000                 7964   
2            3                   4.000                 7964   
3            4                   4.000                 7964   
4            5                   4.000                 7964   
5            6                   4.000                 7964   
6            7                   4.000                 7964   
7            8                   4.000                 7964   
8            9                   4.000                 7964   
9           10                   4.000                 7964   
10          11                   4.000                 7964   
11          12                   5.000                 6212   
12          21                   5.000                 7964   
13          22                   5.000                 7964   
14          23                   5.000                 7964   
15          24                   5.000                 7964   
16          25                   5.000                 7964   
17          26                   5.000                 7964   
18          27                   5.000                 7964   
19          28                   5.000                 7964   
20          29                   5.000                 7964   
21          30                   5.000                 7964   
22          31                   5.000                 7964   
23          32                   5.000                 7964   
24          33                   5.000                 7964   
25          34                   5.000                 7964   
26          35                   4.000                 7239   
27          43                   6.500                 6212   
28          44                   6.500                 6212   
29          45                   6.500                 6212   
30          46                   6.500                 6212   
31          47                   6.500                 6212   
32          48                   6.500                 6212   
33          49                   6.500                 6212   
34          50                   6.500                 6212   
35          51                   3.000                 7239   
36          52                   3.000                 7239   
37          53                   7.000                 7239   
38          54                   7.000                 7239   
39          55                   6.500                 6212   
40          56                   1.600                 6212   
41          57                   1.600                 6212   
42          58                   0.500                 6212   
43          59                   0.750                 6212   
44          60                   1.000                 6212   
45          61                   2.000                 6212   
46          62                   5.000                 6212   
47          63                   0.500                 6212   
48          64                   0.750                 6212   
49          65                   1.000                 6212   
50          66                   2.000                 6212   
51          67                   5.000                 6212   
52          68                   2.000                 7239   
53          75                   4.000                 6212   
54          81                   5.000                 6212   
55          82                   5.000                 6212   
56          83                   5.000                 6212   
57          84                   7.000                 6212   
58          85                   8.500                 6212   
59          86                  10.000                 6212   
60          87                  12.000                 6212   
61          88                  14.000                 6212   
62          89                  16.0

In [103]:
column_names = result_df.columns
print(column_names)


Index(['sample_id', 'solution_concentration', 'solvent_pubchem_cid',
       'polymer_common_name', 'polymer_mw', 'polymer_mn', 'polymer_dispersity',
       'hole_mobility', 'solution_treatment', 'substrate_pretreatment',
       'post_process', 'channel_width', 'channel_length',
       'dielectric_thickness', 'film_deposition_type_Dip Coating',
       'film_deposition_type_blade', 'film_deposition_type_dip',
       'film_deposition_type_drop', 'film_deposition_type_inkjet',
       'film_deposition_type_shear', 'film_deposition_type_spin',
       'film_deposition_type_wire', 'gate_material_Al', 'gate_material_Au',
       'gate_material_PEDOT:PSS', 'gate_material_PET', 'gate_material_Si',
       'gate_material_glass', 'gate_material_n-doped Si',
       'gate_material_p-doped Si', 'dielectric_material_6FDA-DABC',
       'dielectric_material_CYTOP', 'dielectric_material_PAN',
       'dielectric_material_PMMA', 'dielectric_material_PTrFE',
       'dielectric_material_PVP', 'dielectric_materi

Consolidating Descriptors

Coating :

film_deposition_type_MGC (dip,Dip,blade, inkjet, shear, wire)
film_deposition_type_spin
film_deposition_type_drop

Gate Material :

gate_material_n_doped Si = ('gate_material_n-doped Si', 'gate_material_Si','gate_material_p-doped Si')
gate_material_other = ('gate_material_Al', 'gate_material_Au', 'gate_material_PEDOT:PSS', 'gate_material_PET','gate_material_glass')


Dielectric Material :

dielectric_material_SiO2
dielectric_material_other = ('dielectric_material_6FDA-DABC',
       'dielectric_material_CYTOP', 'dielectric_material_PAN',
       'dielectric_material_PMMA', 'dielectric_material_PTrFE',
       'dielectric_material_PVP', 'dielectric_material_Shellac',
       'dielectric_material_Si3N4')




In [104]:

#consolidating gate material columns
gate_material_Si_to_consolidate = ['gate_material_n-doped Si', 'gate_material_Si','gate_material_p-doped Si']
gate_material_other_to_consolidate = ['gate_material_Al', 'gate_material_Au', 'gate_material_PEDOT:PSS', 'gate_material_PET','gate_material_glass']
# Create new columns
result_df['gate_material_Si'] = result_df[gate_material_Si_to_consolidate].max(axis=1)
result_df['gate_material_Other'] = result_df[gate_material_other_to_consolidate].max(axis=1)
# Drop the original columns
result_df.drop(columns=gate_material_Si_to_consolidate, inplace=True)
result_df.drop(columns=gate_material_other_to_consolidate, inplace=True)


#consolidating coating columns
MGC_columns_to_consolidate = ['film_deposition_type_Dip Coating',
                           'film_deposition_type_blade',
                           'film_deposition_type_dip',
                           'film_deposition_type_inkjet',
                           'film_deposition_type_shear',
                           'film_deposition_type_wire']
# Create new columns
result_df['film_deposition_type_MGC'] = result_df[MGC_columns_to_consolidate].max(axis=1)
# Drop the original columns
result_df.drop(columns=MGC_columns_to_consolidate, inplace=True)


#consolidating dielectric columns
dielectric_material_columns_to_consolidate = ['dielectric_material_6FDA-DABC',
       'dielectric_material_CYTOP', 'dielectric_material_PAN',
       'dielectric_material_PMMA', 'dielectric_material_PTrFE',
       'dielectric_material_PVP', 'dielectric_material_Shellac',
       'dielectric_material_Si3N4']
# Create new columns
result_df['dielectric_material_other'] = result_df[dielectric_material_columns_to_consolidate].max(axis=1)
# Drop the original columns
result_df.drop(columns=dielectric_material_columns_to_consolidate, inplace=True)


In [105]:
result_df

sample_id  solution_concentration  solvent_pubchem_cid  \
0            1                   4.000                 7964   
1            2                   4.000                 7964   
2            3                   4.000                 7964   
3            4                   4.000                 7964   
4            5                   4.000                 7964   
5            6                   4.000                 7964   
6            7                   4.000                 7964   
7            8                   4.000                 7964   
8            9                   4.000                 7964   
9           10                   4.000                 7964   
10          11                   4.000                 7964   
11          12                   5.000                 6212   
12          21                   5.000                 7964   
13          22                   5.000                 7964   
14          23                   5.000                 7964   
15          24                   5.000                 7964   
16          25                   5.000                 7964   
17          26                   5.000                 7964   
18          27                   5.000                 7964   
19          28                   5.000                 7964   
20          29                   5.000                 7964   
21          30                   5.000                 7964   
22          31                   5.000                 7964   
23          32                   5.000                 7964   
24          33                   5.000                 7964   
25          34                   5.000                 7964   
26          35                   4.000                 7239   
27          43                   6.500                 6212   
28          44                   6.500                 6212   
29          45                   6.500                 6212   
30          46                   6.500                 6212   
31          47                   6.500                 6212   
32          48                   6.500                 6212   
33          49                   6.500                 6212   
34          50                   6.500                 6212   
35          51                   3.000                 7239   
36          52                   3.000                 7239   
37          53                   7.000                 7239   
38          54                   7.000                 7239   
39          55                   6.500                 6212   
40          56                   1.600                 6212   
41          57                   1.600                 6212   
42          58                   0.500                 6212   
43          59                   0.750                 6212   
44          60                   1.000                 6212   
45          61                   2.000                 6212   
46          62                   5.000                 6212   
47          63                   0.500                 6212   
48          64                   0.750                 6212   
49          65                   1.000                 6212   
50          66                   2.000                 6212   
51          67                   5.000                 6212   
52          68                   2.000                 7239   
53          75                   4.000                 6212   
54          81                   5.000                 6212   
55          82                   5.000                 6212   
56          83                   5.000                 6212   
57          84                   7.000                 6212   
58          85                   8.500                 6212   
59          86                  10.000                 6212   
60          87                  12.000                 6212   
61          88                  14.000                 6212   
62          89                  16.0

In [106]:
## replacing the pubchem_cid with solvent boiling point

# Get unique PubChem CIDs from the 'solvent_pubchem_cid' column
unique_pubchem_cids = result_df['solvent_pubchem_cid'].unique()

# Display the unique PubChem CIDs
print(unique_pubchem_cids)



[ 7964  6212  7239  6591  7809 13229    13  8030  1140  7501   241  6344
  7503]


In [107]:
# Dictionary mapping PubChem CIDs to boiling points
boiling_point_dict = {
    7964: 132,
    6212: 62,
    7239: 180.1,
    6591: 146,
    7809: 138,
    13229: 238,
    13: 213,
    8030: 84,
    1140: 111,
    7501: 145,
    241: 80,
    6344: 40,
    7503: 179
}

# Add a new column "solvent_boiling_point" based on PubChem CIDs
result_df['solvent_boiling_point'] = result_df['solvent_pubchem_cid'].map(boiling_point_dict)


# Drop unnecessary columns that won't be used for modeling
columns_to_drop = ['solvent_pubchem_cid']
result_df = result_df.drop(columns=columns_to_drop)

# Display the resulting DataFrame
result_df


sample_id  solution_concentration polymer_common_name   polymer_mw  \
0            1                   4.000             DPP-DTT     299.0000   
1            2                   4.000             DPP-DTT     299.0000   
2            3                   4.000             DPP-DTT     299.0000   
3            4                   4.000             DPP-DTT     299.0000   
4            5                   4.000             DPP-DTT     299.0000   
5            6                   4.000             DPP-DTT     299.0000   
6            7                   4.000             DPP-DTT     299.0000   
7            8                   4.000             DPP-DTT     299.0000   
8            9                   4.000             DPP-DTT     299.0000   
9           10                   4.000             DPP-DTT     299.0000   
10          11                   4.000             DPP-DTT     299.0000   
11          12                   5.000             DPP-DTT     292.2000   
12          21                   5.000             DPP-DTT      91.0000   
13          22                   5.000             DPP-DTT     344.0000   
14          23                   5.000             DPP-DTT     501.0000   
15          24                   5.000             DPP-DTT     501.0000   
16          25                   5.000             DPP-DTT     501.0000   
17          26                   5.000             DPP-DTT     501.0000   
18          27                   5.000             DPP-DTT     501.0000   
19          28                   5.000             DPP-DTT     501.0000   
20          29                   5.000             DPP-DTT     501.0000   
21          30                   5.000             DPP-DTT     501.0000   
22          31                   5.000             DPP-DTT     501.0000   
23          32                   5.000             DPP-DTT     501.0000   
24          33                   5.000             DPP-DTT     501.0000   
25          34                   5.000             DPP-DTT     501.0000   
26          35                   4.000             DPP-DTT     199.0000   
27          43                   6.500             DPP-DTT      91.0000   
28          44                   6.500             DPP-DTT      91.0000   
29          45                   6.500             DPP-DTT      91.0000   
30          46                   6.500             DPP-DTT      91.0000   
31          47                   6.500             DPP-DTT      91.0000   
32          48                   6.500             DPP-DTT      91.0000   
33          49                   6.500             DPP-DTT      91.0000   
34          50                   6.500             DPP-DTT      91.0000   
35          51                   3.000             DPP-DTT     290.0000   
36          52                   3.000             DPP-DTT     290.0000   
37          53                   7.000             DPP-DTT     290.0000   
38          54                   7.000             DPP-DTT     290.0000   
39          55                   6.500             DPP-DTT     100.0000   
40          56                   1.600             DPP-DTT     279.0000   
41          57                   1.600             DPP-DTT     279.0000   
42          58                   0.500             DPP-DTT     102.0000   
43          59                   0.750             DPP-DTT     102.0000   
44          60                   1.000             DPP-DTT     102.0000   
45          61                   2.000             DPP-DTT     102.0000   
46          62                   5.000             DPP-DTT     102.0000   
47          63                   0.500             DPP-DTT     102.0000   
48          64                   0.750             DPP-DTT     102.0000   
49          65                   1.000             DPP-DTT     102.0000   
50          66                   2.000             DPP-DTT     102.0000   
51          67                   5.000             DPP-DTT     102.0000   
52          68                

In [108]:
# Assuming df is your DataFrame
column_to_move = 'hole_mobility'

# Get the list of columns
columns = list(result_df.columns)

# Move the specified column to the end
columns.remove(column_to_move)
columns.append(column_to_move)

# Reorder the DataFrame columns
result_df = result_df[columns]


In [109]:
column_names = result_df.columns
print(column_names)

Index(['sample_id', 'solution_concentration', 'polymer_common_name',
       'polymer_mw', 'polymer_mn', 'polymer_dispersity', 'solution_treatment',
       'substrate_pretreatment', 'post_process', 'channel_width',
       'channel_length', 'dielectric_thickness', 'film_deposition_type_drop',
       'film_deposition_type_spin', 'dielectric_material_SiO2',
       'electrode_configuration_BGBC', 'electrode_configuration_BGTC',
       'electrode_configuration_TGBC', 'gate_material_Other',
       'film_deposition_type_MGC', 'dielectric_material_other',
       'solvent_boiling_point', 'hole_mobility'],
      dtype='object')


In [110]:
result_df_P3HT = result_df[result_df['polymer_common_name'] == 'P3HT']
result_df_DPP_DTT = result_df[result_df['polymer_common_name'] != 'P3HT']


### P3HT Modeling

In [111]:
result_df_P3HT = result_df_P3HT.drop(columns='polymer_common_name')
result_df_P3HT

sample_id  solution_concentration  polymer_mw  polymer_mn  \
153        350                  10.000         NaN       65.50   
154        351                  10.000         NaN       65.50   
155        352                  10.000         NaN       37.00   
156        353                  10.000         NaN       37.00   
157        354                  10.000         NaN       37.00   
158        355                  10.000         NaN       37.00   
159        356                  10.000         NaN       37.00   
160        357                  10.000         NaN       37.00   
161        358                  10.000         NaN       37.00   
162        359                  10.000         NaN       37.00   
163        360                  10.000         NaN       37.00   
164        361                  10.000     15.4000       10.30   
165        362                  10.000     20.0000       11.10   
166        363                  10.000     22.0000       13.80   
167        364                  10.000     29.0000       19.30   
168        365                  10.000     42.0000       23.30   
169        366                  10.000     52.0000       22.60   
170        367                  10.000     76.0000       44.70   
171        368                  10.000    270.0000      117.40   
172        369                  10.000     15.4000       10.30   
173        370                  10.000     20.0000       11.10   
174        371                  10.000     22.0000       13.80   
175        372                  10.000     29.0000       19.30   
176        373                  10.000     42.0000       23.30   
177        374                  10.000     52.0000       22.60   
178        375                  10.000     76.0000       44.70   
179        376                  10.000    270.0000      117.40   
180        377                  10.000     15.4000       10.30   
181        378                  10.000     20.0000       11.10   
182        379                  10.000     22.0000       13.80   
183        380                  10.000     29.0000       19.30   
184        381                  10.000     42.0000       23.30   
185        382                  10.000     52.0000       22.60   
186        383                  10.000     76.0000       44.70   
187        384                  10.000    270.0000      117.40   
188        385                  10.000     76.0000       44.70   
189        386                  10.000     76.0000       44.70   
190        387                  10.000     76.0000       44.70   
191        388                  10.000     76.0000       44.70   
192        389                  10.000     29.0000       19.30   
193        390                  10.000     29.0000       19.30   
194        391                  10.000     29.0000       19.30   
195        393                  10.000     15.4000       10.30   
196        394                  10.000     15.4000       10.30   
197        395                  10.000     15.4000       10.30   
198        396                  10.000     15.4000       10.30   
199        397                  10.000     29.0000       19.30   
200        398                  10.000     29.0000       19.30   
201        399                  10.000     29.0000       19.30   
202        401                  10.000     15.4000       10.30   
203        402                  10.000     15.4000       10.30   
204        403                  10.000     15.4000       10.30   
205        405                  10.000     76.0000       44.70   
206        406                  10.000     76.0000       44.70   
207        407                  10.000     76.0000       44.70   
208        409                   5.000     91.4810       40.30   
209        410                   5.000     91.4810       40.30   
210        411                   5.000     91.4810       40.30   
211        412                   5.000     91.4810       40.30   
212        413                   5.000     91

In [112]:
num_rows, num_columns = result_df_P3HT.shape
print(f"Number of rows: {num_rows}")
print(f"Number of columns: {num_columns}")


Number of rows: 328
Number of columns: 22


In [113]:
# Identify number of missing values
print(result_df_P3HT.isna().sum(axis=0))
print('Total observations: {}'.format(result_df_P3HT.shape[0]))
print('Total features: {}'.format(result_df_P3HT.shape[1]))

sample_id                         0
solution_concentration           16
polymer_mw                       62
polymer_mn                       24
polymer_dispersity               86
solution_treatment                0
substrate_pretreatment            0
post_process                      0
channel_width                    10
channel_length                   22
dielectric_thickness            151
film_deposition_type_drop         0
film_deposition_type_spin         0
dielectric_material_SiO2          0
electrode_configuration_BGBC      0
electrode_configuration_BGTC      0
electrode_configuration_TGBC      0
gate_material_Other               0
film_deposition_type_MGC          0
dielectric_material_other         0
solvent_boiling_point             0
hole_mobility                     0
dtype: int64
Total observations: 328
Total features: 22


#remove columns that have mostly same values or mostly NaN

* dielectric_material_other
* gate_material_other
* electrode_config_TGBC
* dielectric_thickness



In [114]:
# Assuming result_df_P3HT is your DataFrame
result_df_P3HT = result_df_P3HT.drop(['dielectric_material_other', 'gate_material_Other', 'electrode_configuration_TGBC', 'dielectric_thickness'], axis=1)
num_rows, num_columns = result_df_P3HT.shape
print(f"Number of rows: {num_rows}")
print(f"Number of columns: {num_columns}")

Number of rows: 328
Number of columns: 18


In [115]:
# remove rows with missing values Nan

# Assuming result_df_P3HT is your DataFrame
result_df_P3HT = result_df_P3HT.dropna()

num_rows, num_columns = result_df_P3HT.shape
print(f"Number of rows: {num_rows}")
print(f"Number of columns: {num_columns}")

result_df_P3HT

Number of rows: 224
Number of columns: 18


sample_id  solution_concentration  polymer_mw  polymer_mn  \
164        361                    10.0     15.4000       10.30   
165        362                    10.0     20.0000       11.10   
166        363                    10.0     22.0000       13.80   
167        364                    10.0     29.0000       19.30   
168        365                    10.0     42.0000       23.30   
169        366                    10.0     52.0000       22.60   
170        367                    10.0     76.0000       44.70   
171        368                    10.0    270.0000      117.40   
172        369                    10.0     15.4000       10.30   
173        370                    10.0     20.0000       11.10   
174        371                    10.0     22.0000       13.80   
175        372                    10.0     29.0000       19.30   
176        373                    10.0     42.0000       23.30   
177        374                    10.0     52.0000       22.60   
178        375                    10.0     76.0000       44.70   
179        376                    10.0    270.0000      117.40   
180        377                    10.0     15.4000       10.30   
181        378                    10.0     20.0000       11.10   
182        379                    10.0     22.0000       13.80   
183        380                    10.0     29.0000       19.30   
184        381                    10.0     42.0000       23.30   
185        382                    10.0     52.0000       22.60   
186        383                    10.0     76.0000       44.70   
187        384                    10.0    270.0000      117.40   
188        385                    10.0     76.0000       44.70   
189        386                    10.0     76.0000       44.70   
190        387                    10.0     76.0000       44.70   
191        388                    10.0     76.0000       44.70   
192        389                    10.0     29.0000       19.30   
193        390                    10.0     29.0000       19.30   
194        391                    10.0     29.0000       19.30   
195        393                    10.0     15.4000       10.30   
196        394                    10.0     15.4000       10.30   
197        395                    10.0     15.4000       10.30   
198        396                    10.0     15.4000       10.30   
199        397                    10.0     29.0000       19.30   
200        398                    10.0     29.0000       19.30   
201        399                    10.0     29.0000       19.30   
202        401                    10.0     15.4000       10.30   
203        402                    10.0     15.4000       10.30   
204        403                    10.0     15.4000       10.30   
205        405                    10.0     76.0000       44.70   
206        406                    10.0     76.0000       44.70   
207        407                    10.0     76.0000       44.70   
208        409                     5.0     91.4810       40.30   
209        410                     5.0     91.4810       40.30   
210        411                     5.0     91.4810       40.30   
211        412                     5.0     91.4810       40.30   
212        413                     5.0     91.4810       40.30   
213        414                     5.0     91.4810       40.30   
214        415                     5.0     91.4810       40.30   
215        416                     5.0     91.4810       40.30   
216        417                     5.0     91.4810       40.30   
217        418                     5.0     91.4810       40.30   
218        419                     5.0     91.4810       40.30   
219        420                     5.0     91.4810       40.30   
220        421                     5.0     91.4810       40.30   
221        422                     5.0     91.4810       40.30   
222        423                     5.0     91.4810       40.30   
223        424                     5.0     91

In [121]:
result_df_P3HT.to_excel('result_df_P3HT_1.xlsx', index=True, header=True)


### DPP-DTT Modeling - 1

In [122]:
result_df_DPP_DTT = result_df_DPP_DTT.drop(columns='polymer_common_name')
result_df_DPP_DTT

sample_id  solution_concentration  polymer_mw  polymer_mn  \
0            1                    4.00     299.000   90.000000   
1            2                    4.00     299.000   90.000000   
2            3                    4.00     299.000   90.000000   
3            4                    4.00     299.000   90.000000   
4            5                    4.00     299.000   90.000000   
5            6                    4.00     299.000   90.000000   
6            7                    4.00     299.000   90.000000   
7            8                    4.00     299.000   90.000000   
8            9                    4.00     299.000   90.000000   
9           10                    4.00     299.000   90.000000   
10          11                    4.00     299.000   90.000000   
11          12                    5.00     292.200   74.900000   
12          21                    5.00      91.000   29.000000   
13          22                    5.00     344.000   71.000000   
14          23                    5.00     501.000  110.000000   
15          24                    5.00     501.000  110.000000   
16          25                    5.00     501.000  110.000000   
17          26                    5.00     501.000  110.000000   
18          27                    5.00     501.000  110.000000   
19          28                    5.00     501.000  110.000000   
20          29                    5.00     501.000  110.000000   
21          30                    5.00     501.000  110.000000   
22          31                    5.00     501.000  110.000000   
23          32                    5.00     501.000  110.000000   
24          33                    5.00     501.000  110.000000   
25          34                    5.00     501.000  110.000000   
26          35                    4.00     199.000   55.000000   
27          43                    6.50      91.000   29.000000   
28          44                    6.50      91.000   29.000000   
29          45                    6.50      91.000   29.000000   
30          46                    6.50      91.000   29.000000   
31          47                    6.50      91.000   29.000000   
32          48                    6.50      91.000   29.000000   
33          49                    6.50      91.000   29.000000   
34          50                    6.50      91.000   29.000000   
35          51                    3.00     290.000  143.000000   
36          52                    3.00     290.000  143.000000   
37          53                    7.00     290.000  143.000000   
38          54                    7.00     290.000  143.000000   
39          55                    6.50     100.000   67.000000   
40          56                    1.60     279.000   77.000000   
41          57                    1.60     279.000   77.000000   
42          58                    0.50     102.000   43.000000   
43          59                    0.75     102.000   43.000000   
44          60                    1.00     102.000   43.000000   
45          61                    2.00     102.000   43.000000   
46          62                    5.00     102.000   43.000000   
47          63                    0.50     102.000   43.000000   
48          64                    0.75     102.000   43.000000   
49          65                    1.00     102.000   43.000000   
50          66                    2.00     102.000   43.000000   
51          67                    5.00     102.000   43.000000   
52          68                    2.00     250.000         NaN   
53          75                    4.00     350.000  125.000000   
54          81                    5.00         NaN         NaN   
55          82                    5.00         NaN         NaN   
56          83                    5.00     104.000   20.000000   
57          84                    7.00     104.000   20.000000   
58          85                    8.50     104.000   20.000000   
59          86                   10.00     10

In [123]:
num_rows, num_columns = result_df_DPP_DTT.shape
print(f"Number of rows: {num_rows}")
print(f"Number of columns: {num_columns}")


Number of rows: 186
Number of columns: 22


In [124]:
# Identify number of missing values
print(result_df_DPP_DTT.isna().sum(axis=0))
print('Total observations: {}'.format(result_df_DPP_DTT.shape[0]))
print('Total features: {}'.format(result_df_DPP_DTT.shape[1]))


sample_id                        0
solution_concentration           0
polymer_mw                       3
polymer_mn                       4
polymer_dispersity               4
solution_treatment               0
substrate_pretreatment           0
post_process                     0
channel_width                    4
channel_length                   4
dielectric_thickness            45
film_deposition_type_drop        0
film_deposition_type_spin        0
dielectric_material_SiO2         0
electrode_configuration_BGBC     0
electrode_configuration_BGTC     0
electrode_configuration_TGBC     0
gate_material_Other              0
film_deposition_type_MGC         0
dielectric_material_other        0
solvent_boiling_point            0
hole_mobility                    0
dtype: int64
Total observations: 186
Total features: 22


#remove columns that have mostly same values or mostly NaN

* film_deposition_type_drop
* dielectric_thickness


In [125]:
# Assuming result_df_P3HT is your DataFrame
result_df_DPP_DTT = result_df_DPP_DTT.drop(['film_deposition_type_drop', 'dielectric_thickness'], axis=1)
num_rows, num_columns = result_df_DPP_DTT.shape
print(f"Number of rows: {num_rows}")
print(f"Number of columns: {num_columns}")

Number of rows: 186
Number of columns: 20


In [126]:
# remove rows with missing values Nan

# Assuming result_df_DPP-DTT is your DataFrame
result_df_DPP_DTT = result_df_DPP_DTT.dropna()

num_rows, num_columns = result_df_DPP_DTT.shape
print(f"Number of rows: {num_rows}")
print(f"Number of columns: {num_columns}")

result_df_DPP_DTT

Number of rows: 178
Number of columns: 20


sample_id  solution_concentration  polymer_mw  polymer_mn  \
0            1                    4.00     299.000   90.000000   
1            2                    4.00     299.000   90.000000   
2            3                    4.00     299.000   90.000000   
3            4                    4.00     299.000   90.000000   
4            5                    4.00     299.000   90.000000   
5            6                    4.00     299.000   90.000000   
6            7                    4.00     299.000   90.000000   
7            8                    4.00     299.000   90.000000   
8            9                    4.00     299.000   90.000000   
9           10                    4.00     299.000   90.000000   
10          11                    4.00     299.000   90.000000   
11          12                    5.00     292.200   74.900000   
15          24                    5.00     501.000  110.000000   
16          25                    5.00     501.000  110.000000   
17          26                    5.00     501.000  110.000000   
18          27                    5.00     501.000  110.000000   
19          28                    5.00     501.000  110.000000   
20          29                    5.00     501.000  110.000000   
21          30                    5.00     501.000  110.000000   
22          31                    5.00     501.000  110.000000   
23          32                    5.00     501.000  110.000000   
24          33                    5.00     501.000  110.000000   
25          34                    5.00     501.000  110.000000   
26          35                    4.00     199.000   55.000000   
27          43                    6.50      91.000   29.000000   
28          44                    6.50      91.000   29.000000   
29          45                    6.50      91.000   29.000000   
30          46                    6.50      91.000   29.000000   
31          47                    6.50      91.000   29.000000   
32          48                    6.50      91.000   29.000000   
33          49                    6.50      91.000   29.000000   
34          50                    6.50      91.000   29.000000   
35          51                    3.00     290.000  143.000000   
36          52                    3.00     290.000  143.000000   
37          53                    7.00     290.000  143.000000   
38          54                    7.00     290.000  143.000000   
39          55                    6.50     100.000   67.000000   
40          56                    1.60     279.000   77.000000   
41          57                    1.60     279.000   77.000000   
42          58                    0.50     102.000   43.000000   
43          59                    0.75     102.000   43.000000   
44          60                    1.00     102.000   43.000000   
45          61                    2.00     102.000   43.000000   
46          62                    5.00     102.000   43.000000   
47          63                    0.50     102.000   43.000000   
48          64                    0.75     102.000   43.000000   
49          65                    1.00     102.000   43.000000   
50          66                    2.00     102.000   43.000000   
51          67                    5.00     102.000   43.000000   
56          83                    5.00     104.000   20.000000   
57          84                    7.00     104.000   20.000000   
58          85                    8.50     104.000   20.000000   
59          86                   10.00     104.000   20.000000   
60          87                   12.00     104.000   20.000000   
61          88                   14.00     104.000   20.000000   
62          89                   16.00     104.000   20.000000   
63          90                   18.00     104.000   20.000000   
64          91                   25.00     104.000   20.000000   
65          92                    5.00     104.000   20.000000   
66          93                    7.00     10

In [ ]:
result_df_DPP_DTT.to_excel('result_df_P3HT_1.xlsx', index=True, header=True)

In [ ]:
#### 